# Proyek Semantik Web: Data for Top 250 Movie by IMDb

### Import Library

In [1]:
import pandas as pd
import itertools

import requests
from bs4 import BeautifulSoup
import urllib.parse
import time
from urllib3.util.retry import Retry
from requests.adapters import HTTPAdapter

### Loading Data

In [2]:
#https://www.kaggle.com/datasets/karkavelrajaj/imdb-top-250-movies
imdb_df = pd.read_csv('data\movies.csv')
imdb_df.head()

rank   movie_id                     title  year  \
0     1  tt0111161  The Shawshank Redemption  1994   
1     2  tt0068646             The Godfather  1972   
2     3  tt0468569           The Dark Knight  2008   
3     4  tt0071562     The Godfather Part II  1974   
4     5  tt0050083              12 Angry Men  1957   

                                   link imbd_votes  imbd_rating certificate  \
0  https://www.imdb.com/title/tt0111161  2,711,075          9.3           R   
1  https://www.imdb.com/title/tt0068646  1,882,829          9.2           R   
2  https://www.imdb.com/title/tt0468569  2,684,051          9.0       PG-13   
3  https://www.imdb.com/title/tt0071562  1,285,350          9.0           R   
4  https://www.imdb.com/title/tt0050083    800,954          9.0    Approved   

  duration               genre  ... director_id         director_name  \
0   2h 22m               Drama  ...   nm0001104        Frank Darabont   
1   2h 55m         Crime,Drama  ...   nm0000338  Francis Ford Coppola   
2   2h 32m  Action,Crime,Drama  ...   nm0634240     Christopher Nolan   
3   3h 22m         Crime,Drama  ...   nm0000338  Francis Ford Coppola   
4   1h 36m         Crime,Drama  ...   nm0001486          Sidney Lumet   

                                           writer_id  \
0                                nm0000175,nm0001104   
1                                nm0701374,nm0000338   
2  tt0468569,nm0634300,nm0634240,nm0275286,tt0468569   
3                                nm0000338,nm0701374   
4                                          nm0741627   

                                         writer_name  \
0                        Stephen King,Frank Darabont   
1                    Mario Puzo,Francis Ford Coppola   
2  Writers,Jonathan Nolan,Christopher Nolan,David...   
3                    Francis Ford Coppola,Mario Puzo   
4                                      Reginald Rose   

                                           storyline  \
0  Over the course of several years, two convicts...   
1  The aging patriarch of an organized crime dyna...   
2  When the menace known as the Joker wreaks havo...   
3  The early life and career of Vito Corleone in ...   
4  The jury in a New York City murder trial is fr...   

                                             user_id  \
0  ur16161013,ur15311310,ur0265899,ur16117882,ur1...   
1  ur24740649,ur86182727,ur15794099,ur15311310,ur...   
2  ur87850731,ur1293485,ur129557514,ur12449122,ur...   
3  ur0176092,ur0688559,ur92260614,ur0200644,ur117...   
4  ur1318549,ur0643062,ur0688559,ur20552756,ur945...   

                                           user_name  \
0  hitchcockthelegend,Sleepin_Dragon,EyeDunno,ale...   
1  CalRhys,andrewburgereviews,gogoschka-1,Sleepin...   
2  MrHeraclius,Smells_Like_Cheese,dseferaj,little...   
3  Nazi_Fighter_David,tfrizzell,umunir-36959,DanB...   
4  uds3,tedg,tfrizzell,TheLittleSongbird,henrique...   

                                           review_id  \
0  rw2284594,rw6606154,rw1221355,rw1822343,rw1288...   
1  rw3038370,rw4756923,rw4059579,rw6568526,rw1897...   
2  rw5478826,rw1914442,rw6606026,rw1917099,rw5170...   
3  rw0135607,rw0135487,rw5049900,rw0135526,rw0135...   
4  rw0060044,rw0060025,rw0060034,rw2262425,rw5448...   

                                        review_title  \
0  Some birds aren't meant to be caged.,An incred...   
1  The Pinnacle Of Flawless Films!,An offer so go...   
2  The Dark Knight,The Batman of our dreams! So m...   
3  Breathtaking in its scope and tragic grandeur....   
4  The over-used term "classic movie" really come...   

                                      review_content  
0  The Shawshank Redemption is written and direct...  
1  'The Godfather' is the pinnacle of flawless fi...  
2  Confidently directed, dark, brooding, and pack...  
3  Coppola's masterpiece is rivaled only by "The ...  
4  This once-in-a-generation masterpiece simply h...  

[5 rows x 22 columns]

### Menilai Data

In [3]:
imdb_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 22 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   rank            250 non-null    int64  
 1   movie_id        250 non-null    object 
 2   title           250 non-null    object 
 3   year            250 non-null    int64  
 4   link            250 non-null    object 
 5   imbd_votes      250 non-null    object 
 6   imbd_rating     250 non-null    float64
 7   certificate     249 non-null    object 
 8   duration        250 non-null    object 
 9   genre           250 non-null    object 
 10  cast_id         250 non-null    object 
 11  cast_name       250 non-null    object 
 12  director_id     250 non-null    object 
 13  director_name   250 non-null    object 
 14  writer_id       250 non-null    object 
 15  writer_name     250 non-null    object 
 16  storyline       250 non-null    object 
 17  user_id         250 non-null    obj

*Masih terdapat data yang tidak akan digunakan: movie_id, certificate, cast_id, director_id, writer_id, user_id, user_name, review_id, review_title, review_content*<br />
*Nama data 'link' perlu diubah menjadi 'imdb_link'*

### Mengubah Data

In [4]:
#Hapus data yang tidak digunakan
columns_to_drop = [
    'movie_id', 'certificate', 'cast_id', 'director_id', 'writer_id', 'user_id',
    'user_name', 'review_id', 'review_title', 'review_content'
]

imdb_df = imdb_df.drop(columns=columns_to_drop)

imdb_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 12 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   rank           250 non-null    int64  
 1   title          250 non-null    object 
 2   year           250 non-null    int64  
 3   link           250 non-null    object 
 4   imbd_votes     250 non-null    object 
 5   imbd_rating    250 non-null    float64
 6   duration       250 non-null    object 
 7   genre          250 non-null    object 
 8   cast_name      250 non-null    object 
 9   director_name  250 non-null    object 
 10  writer_name    250 non-null    object 
 11  storyline      250 non-null    object 
dtypes: float64(1), int64(2), object(9)
memory usage: 23.6+ KB


In [5]:
#Mengubah nama data 'link'
imdb_df = imdb_df.rename(columns={'link': 'imdb_link'})

imdb_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 12 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   rank           250 non-null    int64  
 1   title          250 non-null    object 
 2   year           250 non-null    int64  
 3   imdb_link      250 non-null    object 
 4   imbd_votes     250 non-null    object 
 5   imbd_rating    250 non-null    float64
 6   duration       250 non-null    object 
 7   genre          250 non-null    object 
 8   cast_name      250 non-null    object 
 9   director_name  250 non-null    object 
 10  writer_name    250 non-null    object 
 11  storyline      250 non-null    object 
dtypes: float64(1), int64(2), object(9)
memory usage: 23.6+ KB


In [6]:
#Menambahkan Tabel Person (person_df)
def get_unique_person_names(df, columns):
    all_names = set()
    for column in columns:
        df[column].dropna().apply(lambda x: all_names.update(name.strip() for name in x.split(',')))
    return list(all_names)

columns = ['director_name', 'cast_name', 'writer_name']

unique_person_names = get_unique_person_names(imdb_df, columns)

unique_person_names = [name for name in unique_person_names if name.strip()]

person_df = pd.DataFrame(unique_person_names, columns=['person_name'])

print(person_df)

             person_name
0        Morgan Strebler
1             Sean Frank
2          Helena Barlow
3        Kiersten Dolbec
4          Afemo Omilami
...                  ...
16738         Steve Kish
16739     Joanne Genthon
16740  Brian Reed Garvin
16741    Hiroshi Unayama
16742       Robert Blake

[16743 rows x 1 columns]


In [7]:
#Menambahkan Tabel Genre (genre_df)
def get_unique_genres(df):
    all_genres = set()
    df['genre'].dropna().apply(lambda x: all_genres.update(genre.strip() for genre in x.split(',')))
    return list(all_genres)

unique_genres = get_unique_genres(imdb_df)

genre_df = pd.DataFrame(unique_genres, columns=['genre'])

print(genre_df)

        genre
0       Sport
1    Thriller
2      Horror
3   Biography
4      Comedy
5      Action
6         War
7       Music
8       Crime
9     Romance
10     Sci-Fi
11  Animation
12    Fantasy
13    Western
14  Film-Noir
15    Musical
16      Drama
17    History
18  Adventure
19     Family
20    Mystery


### Menambahkan Data

#### Data Rating, Link rottentomatoes, dan Poster
Scrape dari rottentomatoes.com

In [8]:
def search_rotten_tomatoes(title, year):
    print(f"Searching for the movie '{title}' ({year}) on Rotten Tomatoes...")

    search_url = f"https://www.rottentomatoes.com/search?search={urllib.parse.quote(title)}"
    response = requests.get(search_url)
    if response.status_code == 200:
        soup = BeautifulSoup(response.text, 'html.parser')
        search_results = soup.find_all('search-page-media-row')

        if search_results:
            for result in search_results:
                movie_url_tag = result.find('a', class_='unset', attrs={'data-qa': 'info-name'})
                movie_url = movie_url_tag['href'] if movie_url_tag else None
                movie_year = result.get('releaseyear', '').strip()
                
                if movie_url and movie_year == str(year):
                    full_movie_url = f"{movie_url}"
                    print(f"Found URL for '{title}' ({year}) using search: {full_movie_url}")
                    return full_movie_url

            print(f"No matching year found for '{title}' on Rotten Tomatoes.")
        else:
            print(f"No search results found for '{title}' on Rotten Tomatoes.")

    print(f"Failed to find URL for '{title}' on Rotten Tomatoes.")
    return None

In [9]:
def scrape_rotten_tomatoes(url):
    print(f"Scraping data from URL: {url}...")
    response = requests.get(url)
    if response.status_code != 200:
        print(f"Failed to scrape data from '{url}' (status code: {response.status_code}).")
        return 'N/A', 'N/A', 'N/A', 'N/A'
    
    soup = BeautifulSoup(response.text, 'html.parser')
    
    rating_tag = soup.find('rt-button', {'slot': 'audienceScore'})
    rating = rating_tag.text.strip() if rating_tag else 'N/A'
    
    votes_tag = soup.find('rt-link', {'slot': 'audienceReviews'})
    votes = votes_tag.text.strip() if votes_tag else 'N/A'
    
    image_tag = soup.find('rt-img', {'slot': 'posterImage'})
    image_link = image_tag['src'] if image_tag else 'N/A'
    
    print(f"Scrape result: {rating}, votes: {votes}, image link: {image_link}, link: {url}")
    return rating, votes, image_link, url

In [10]:
rotten_ratings = []
rotten_votes = []
rotten_link = []
poster = []

for index, row in imdb_df.iterrows():
    title = row['title']
    year = row['year']
    
    print(f"\nProcessing movie: {title}")
    start_time = time.time()
    
    url = search_rotten_tomatoes(title, year)
    if url:
        rating, votes, poster_link, link = scrape_rotten_tomatoes(url)
    else:
        rating, votes, poster_link, link = 'N/A', 'N/A', 'N/A', 'N/A'
    
    rotten_ratings.append(rating)
    rotten_votes.append(votes)
    rotten_link.append(link)
    poster.append(poster_link)

    end_time = time.time()
    print(f"Completed processing '{title}' in {end_time - start_time:.2f} seconds.")

rotten_rate_df = pd.DataFrame({
    'title': imdb_df['title'],
    'rotten_rating': rotten_ratings,
    'rotten_votes': rotten_votes,
    'rotten_link': rotten_link,
    'poster' : poster
})

print("\nScraping process completed. Here are the results:")
print(rotten_rate_df)


Processing movie: The Shawshank Redemption
Searching for the movie 'The Shawshank Redemption' (1994) on Rotten Tomatoes...
Found URL for 'The Shawshank Redemption' (1994) using search: https://www.rottentomatoes.com/m/shawshank_redemption
Scraping data from URL: https://www.rottentomatoes.com/m/shawshank_redemption...
Scrape result: 98%, votes: 250,000+ Ratings, image link: https://resizing.flixster.com/AKxrfDANaBRnffewUyMm3jPbMtU=/206x305/v2/https://resizing.flixster.com/-XZAfHZM39UwaGJIFWKAE8fS0ak=/v3/t/assets/p15987_p_v12_at.jpg, link: https://www.rottentomatoes.com/m/shawshank_redemption
Completed processing 'The Shawshank Redemption' in 1.73 seconds.

Processing movie: The Godfather
Searching for the movie 'The Godfather' (1972) on Rotten Tomatoes...
Found URL for 'The Godfather' (1972) using search: https://www.rottentomatoes.com/m/the_godfather
Scraping data from URL: https://www.rottentomatoes.com/m/the_godfather...
Scrape result: 98%, votes: 250,000+ Ratings, image link: http

In [11]:
rotten_rate_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 5 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   title          250 non-null    object
 1   rotten_rating  250 non-null    object
 2   rotten_votes   250 non-null    object
 3   rotten_link    250 non-null    object
 4   poster         250 non-null    object
dtypes: object(5)
memory usage: 9.9+ KB


In [12]:
condition_rating = (rotten_rate_df['rotten_rating'] == 'N/A') | (~rotten_rate_df['rotten_rating'].str.contains('%'))
condition_votes = (rotten_rate_df['rotten_votes'] == 'N/A') | (~rotten_rate_df['rotten_votes'].str.contains('\+'))
condition_link = (rotten_rate_df['rotten_link'] == 'N/A')
condition_poster = (rotten_rate_df['poster'] == 'N/A')

filtered_df = rotten_rate_df[condition_rating | condition_votes | condition_link | condition_poster]

print(filtered_df)


                              title rotten_rating           rotten_votes  \
9    The Good, the Bad and the Ugly           N/A                    N/A   
27                        Star Wars           N/A                    N/A   
93                         The Hunt           N/A                    N/A   
95                                M           N/A                    N/A   
127                         The Kid           N/A                    N/A   
152                       The Thing           N/A                    N/A   
157                  V for Vendetta           N/A                    N/A   
186                     The General           N/A                    N/A   
233                        Jai Bhim           98%  Fewer than 50 Ratings   

                                   rotten_link  \
9                                          N/A   
27                                         N/A   
93                                         N/A   
95                                     

In [21]:
filtered_df.to_csv('result-data/temp.csv', index=False)

In [24]:
#Mengisi filtered_df dan mengload kembali setelah diisi manual
filled_df = pd.read_csv('result-data/temp_filled.csv')
filled_df.head()

title rotten_rating      rotten_votes  \
0  The Good, the Bad and the Ugly           97%  100,000+ Ratings   
1                       Star Wars           97%  250,000+ Ratings   
2                        The Hunt           93%   10,000+ Ratings   
3                               M           95%   25,000+ Ratings   
4                         The Kid           95%   10,000+ Ratings   

                                         rotten_link  \
0  https://www.rottentomatoes.com/m/the_good_the_...   
1  https://www.rottentomatoes.com/franchise/star_...   
2     https://www.rottentomatoes.com/m/the_hunt_2013   
3         https://www.rottentomatoes.com/m/1012928-m   
4       https://www.rottentomatoes.com/m/1052609-kid   

                                              poster  
0  https://resizing.flixster.com/h5AIpcBoZyRptoMk...  
1  https://resizing.flixster.com/oMsdTq3UaKH3TxTf...  
2  https://resizing.flixster.com/ZHjg0SeHTXFEI_VE...  
3  https://resizing.flixster.com/rVDuqcxlvS8She3L...  
4  https://resizing.flixster.com/TNWW5OlgDxUz2_5_...

In [25]:
filled_df['rotten_rating'] = filled_df['rotten_rating'].astype(str)
filled_df['rotten_votes'] = filled_df['rotten_votes'].astype(str)
filled_df['rotten_link'] = filled_df['rotten_link'].astype(str)
filled_df['poster'] = filled_df['poster'].astype(str)

# Merge filled_df ke rotten_df
rotten_rate_df = rotten_rate_df.merge(filled_df, on='title', how='left', suffixes=('_rotten', '_filled'))

rotten_rate_df['rotten_rating'] = rotten_rate_df['rotten_rating_filled'].combine_first(rotten_rate_df['rotten_rating_rotten'])
rotten_rate_df['rotten_votes'] = rotten_rate_df['rotten_votes_filled'].combine_first(rotten_rate_df['rotten_votes_rotten'])
rotten_rate_df['rotten_link'] = rotten_rate_df['rotten_link_filled'].combine_first(rotten_rate_df['rotten_link_rotten'])
rotten_rate_df['poster'] = rotten_rate_df['poster_filled'].combine_first(rotten_rate_df['poster_rotten'])

rotten_rate_df = rotten_rate_df.drop(columns=['rotten_rating_rotten', 'rotten_votes_rotten', 'rotten_link_rotten', 'poster_rotten', 'rotten_rating_filled', 'rotten_votes_filled', 'rotten_link_filled', 'poster_filled'])

rotten_rate_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250 entries, 0 to 249
Data columns (total 5 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   title          250 non-null    object
 1   rotten_rating  250 non-null    object
 2   rotten_votes   250 non-null    object
 3   rotten_link    250 non-null    object
 4   poster         250 non-null    object
dtypes: object(5)
memory usage: 9.9+ KB


In [26]:
movie_df = imdb_df.merge(rotten_rate_df, on='title', how='left')
movie_df.head()

rank                     title  year                             imdb_link  \
0     1  The Shawshank Redemption  1994  https://www.imdb.com/title/tt0111161   
1     2             The Godfather  1972  https://www.imdb.com/title/tt0068646   
2     3           The Dark Knight  2008  https://www.imdb.com/title/tt0468569   
3     4     The Godfather Part II  1974  https://www.imdb.com/title/tt0071562   
4     5              12 Angry Men  1957  https://www.imdb.com/title/tt0050083   

  imbd_votes  imbd_rating duration               genre  \
0  2,711,075          9.3   2h 22m               Drama   
1  1,882,829          9.2   2h 55m         Crime,Drama   
2  2,684,051          9.0   2h 32m  Action,Crime,Drama   
3  1,285,350          9.0   3h 22m         Crime,Drama   
4    800,954          9.0   1h 36m         Crime,Drama   

                                           cast_name         director_name  \
0  Tim Robbins,Morgan Freeman,Bob Gunton,William ...        Frank Darabont   
1  Marlon Brando,Al Pacino,James Caan,Richard S. ...  Francis Ford Coppola   
2  Christian Bale,Heath Ledger,Aaron Eckhart,Mich...     Christopher Nolan   
3  Al Pacino,Robert Duvall,Diane Keaton,Robert De...  Francis Ford Coppola   
4  Martin Balsam,John Fiedler,Lee J. Cobb,E.G. Ma...          Sidney Lumet   

                                         writer_name  \
0                        Stephen King,Frank Darabont   
1                    Mario Puzo,Francis Ford Coppola   
2  Writers,Jonathan Nolan,Christopher Nolan,David...   
3                    Francis Ford Coppola,Mario Puzo   
4                                      Reginald Rose   

                                           storyline rotten_rating  \
0  Over the course of several years, two convicts...           98%   
1  The aging patriarch of an organized crime dyna...           98%   
2  When the menace known as the Joker wreaks havo...           94%   
3  The early life and career of Vito Corleone in ...           97%   
4  The jury in a New York City murder trial is fr...           97%   

       rotten_votes                                        rotten_link  \
0  250,000+ Ratings  https://www.rottentomatoes.com/m/shawshank_red...   
1  250,000+ Ratings     https://www.rottentomatoes.com/m/the_godfather   
2  250,000+ Ratings   https://www.rottentomatoes.com/m/the_dark_knight   
3  250,000+ Ratings  https://www.rottentomatoes.com/m/godfather_par...   
4  100,000+ Ratings  https://www.rottentomatoes.com/m/1000013_12_an...   

                                              poster  
0  https://resizing.flixster.com/AKxrfDANaBRnffew...  
1  https://resizing.flixster.com/bl70zh3G-M0o6pC2...  
2  https://resizing.flixster.com/dJM7TJzf7qEp9NA2...  
3  https://resizing.flixster.com/lQFJ7WL7yvGucQ89...  
4  https://resizing.flixster.com/FDNKxkwCqhqdzh-I...

#### Data Person
Scrape dari themoviedb.org

In [13]:
session = requests.Session()

retry = Retry(
    total=5,
    backoff_factor=1,
    status_forcelist=[429, 500, 502, 503, 504],
    raise_on_status=False
)
adapter = HTTPAdapter(max_retries=retry)
session.mount("https://", adapter)
session.mount("http://", adapter)

In [17]:
def search_person(person_name):
    print(f"Searching for {person_name} on The Movie Database...")

    # Generate combinations of the name
    name_parts = person_name.split()
    combinations = []
    for r in range(2, len(name_parts) + 1):
        combinations.extend(list(itertools.combinations(name_parts, r)))

    # Try searching for each combination
    for combination in combinations:
        combined_name = ' '.join(combination)
        search_url = f"https://www.themoviedb.org/search?query={urllib.parse.quote(combined_name)}"
        while True:
            try:
                response = session.get(search_url, timeout=10)
                response.raise_for_status()  # Raise an exception for HTTP errors

                if response.status_code == 200:
                    soup = BeautifulSoup(response.content, 'html.parser')
                    results = soup.find_all('a', class_='result')
                    for result in results:
                        if combined_name.lower() in result.text.lower() and result['href'].startswith('/person/'):
                            person_link = result['href']
                            print(f"Found link for {person_name}: {person_link}")
                            return person_link
                        
                    break

            except requests.exceptions.RequestException as e:
                print(f"Error occurred during search for {combined_name}: {e}")
                print("Pausing for 10 minutes before retrying...")
                time.sleep(600)
                continue
            
    print(f"No results found for {person_name} on The Movie Database.")
    return None

In [15]:
def scrape_person_info(person_link):
    if person_link:
        profile_url = f"https://www.themoviedb.org{person_link}"
        while True:
            try:
                response = session.get(profile_url, timeout=10)
                response.raise_for_status()  # Raise an exception for HTTP errors

                if response.status_code == 200:
                    soup = BeautifulSoup(response.content, 'html.parser')
                    
                    picture_tag = soup.find('img', class_='profile')
                    picture = picture_tag['src'] if picture_tag else 'N/A'
                    
                    birthday_tag = soup.find('bdi',string='Kelahiran')
                    birthday = birthday_tag.parent.parent.text.replace("Kelahiran","").strip() if birthday_tag else 'N/A'
                    
                    place_of_birth_tag = soup.find('bdi',string='Lokasi Kelahiran')
                    place_of_birth = place_of_birth_tag.parent.parent.text.replace("Lokasi Kelahiran","").strip() if place_of_birth_tag else 'N/A'
                    
                    print(f"Scraped info for {person_link}: Picture - {picture}, Birthday - {birthday}, Place of Birth - {place_of_birth}, Link - {profile_url}")
                    return picture, birthday, place_of_birth, profile_url
                
            except requests.exceptions.RequestException as e:
                print(f"Error occurred during scraping: {e}")
                print("Pausing for 10 minutes before retrying...")
                time.sleep(600)
                continue
    
    print(f"Failed to scrape info for {person_link}.")
    return 'N/A', 'N/A', 'N/A', 'N/A'

In [18]:
person_df['birthday'] = 'N/A'
person_df['place_birth'] = 'N/A'
person_df['picture'] = 'N/A'
person_df['profile_link'] = 'N/A'

for index, row in person_df.iterrows():
    person_name = row['person_name']
    print(f"\nProcessing person: {person_name}")
    start_time = time.time()
    
    person_link = search_person(person_name)
    if person_link:
        picture, birthday, place_birth, profile_link = scrape_person_info(person_link)
    else:
        picture, birthday, place_birth, profile_link = 'N/A', 'N/A', 'N/A', 'N/A'
    
    person_df.at[index, 'picture'] = picture
    person_df.at[index, 'birthday'] = birthday
    person_df.at[index, 'place_birth'] = place_birth
    person_df.at[index, 'profile_link'] = profile_link
    
    end_time = time.time()
    print(f"Completed processing '{person_name}' in {end_time - start_time:.2f} seconds.")

print(person_df)


Processing person: Morgan Strebler
Searching for Morgan Strebler on The Movie Database...
No results found for Morgan Strebler on The Movie Database.
Completed processing 'Morgan Strebler' in 0.48 seconds.

Processing person: Sean Frank
Searching for Sean Frank on The Movie Database...
Found link for Sean Frank: /person/2101527-sean-frank
Scraped info for /person/2101527-sean-frank: Picture - N/A, Birthday - -, Place of Birth - -, Link - https://www.themoviedb.org/person/2101527-sean-frank
Completed processing 'Sean Frank' in 0.84 seconds.

Processing person: Helena Barlow
Searching for Helena Barlow on The Movie Database...
Found link for Helena Barlow: /person/561247-helena-barlow
Scraped info for /person/561247-helena-barlow: Picture - https://media.themoviedb.org/t/p/w300_and_h450_bestv2/upzoPl2SbcjhE5ZO4eF1wi3X9Iw.jpg, Birthday - September  5, 1998 (25 years old), Place of Birth - London, England, UK, Link - https://www.themoviedb.org/person/561247-helena-barlow
Completed process

In [19]:
person_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16743 entries, 0 to 16742
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   person_name   16743 non-null  object
 1   birthday      16743 non-null  object
 2   place_birth   16743 non-null  object
 3   picture       16743 non-null  object
 4   profile_link  16743 non-null  object
dtypes: object(5)
memory usage: 654.2+ KB


In [20]:
person_df.to_csv('result-data/person.csv', index=False)

### Exporting Data

In [1]:
#Final Data: movie_df, genre_df, person_df
person_df.to_csv('result-data/person.csv', index=False)
movie_df.to_csv('result-data/movies.csv', index=False)
genre_df.to_csv('result-data/genres.csv', index=False)

NameError: name 'movie_df' is not defined